In [1]:
import numpy as np
import plotly.graph_objects as go
import plotly.figure_factory as ff
import gmsh
import os
from scipy.spatial import Voronoi
from pebi_gmsh.utils_3D.plane_densityfield import line_distance, point_distance
from pebi_gmsh.utils_3D.sphere_intersection import sphere_intersections
from pebi_gmsh.constraints_3D.constrained_edges import ConstrainedEdgeCollection
from pebi_gmsh.constraints_3D.triangulated_surface import TriangulatedSurface
from pebi_gmsh.utils_3D.plane_densityfield import triangle_inscribed_circle_field

def get_sphere_points(center, radius, theta_res = 100, tau_res = 50):
    theta = np.linspace(0,2*np.pi, theta_res, endpoint=True)
    tau = np.linspace(0, np.pi, tau_res, endpoint=True)

    theta, tau = np.meshgrid(theta, tau)
    z = radius*np.cos(tau) + center[2]
    r = radius*np.sin(tau)
    x = r * np.cos(theta) + center[0]
    y = r * np.sin(theta) + center[1]

    return (x,y,z)
    # points = np.c_[x.flatten(),y.flatten(),z.flatten()]

def get_circle_points(center, tangent1, tangent2, radius_factor = 1):
    radius = np.linalg.norm(center-tangent1)
    dir_1 = (tangent1 - center)/np.linalg.norm(tangent1 - center)
    dir_2 = tangent2-center
    dir_2 = dir_2 - np.dot(dir_2,dir_1)*dir_1
    dir_2 = dir_2/np.linalg.norm(dir_2)

    angles = np.linspace(0,2*np.pi, 100)

    return center.reshape(-1,3) + radius_factor * radius * (np.cos(angles).reshape(-1,1)*dir_1 + np.sin(angles).reshape(-1,1)*dir_2)


### Plane to plane

In [2]:


### Inscribed circle field plane to plane
data = []

base_square = np.array([
    [0,0,-0.02],
    [1,0,-0.02],
    [1,1,-0.02],
    [0,1,-0.02],
])
base_tris = np.array([
    [0,1,2],
    [2,3,0]
])

# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

triangle = np.array([
    [0.2, 0.15, 0.15],
    [0.5, 0.15, 0.8],
    [0.8, 0.15, 0.15],
])
tri = np.array([[0,1,2]])

# Adding triangle
data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    
    i = tri[:,0],
    j = tri[:,1],
    k = tri[:,2],
    color="white",
    showlegend=False

))

#Adding triangle borders and points
data.append(go.Scatter3d(
    x=np.r_[triangle[:,0], triangle[0,0]], 
    y=np.r_[triangle[:,1], triangle[0,1]], 
    z=np.r_[triangle[:,2], triangle[0,2]],
    mode="markers+lines",
    marker=dict(
        color="red",
        size=4
    ),
    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
    
))

center = np.array([0.5,0.5,0.35])
radius = 0.344
sphere_points = get_sphere_points(center, radius)

# Adding sphere
data.append(go.Surface(
    x = sphere_points[0],
    y = sphere_points[1],
    z = sphere_points[2],

    colorscale=[[0, "cyan"], [1, "black"]],
    surfacecolor = np.zeros(sphere_points[0].shape),
    # color = "cyan",
    opacity = 0.2,
    showscale=False,
))

plane_center = [0.5, 0.5, 0]

target_center = [0.5, 0.15, 0.35]

# Adding plane and trigangle normals

data.append(go.Scatter3d(
    x=np.r_[plane_center[0], center[0]], 
    y=np.r_[plane_center[1], center[1]], 
    z=np.r_[plane_center[2], center[2]],
    mode="lines",
    line=dict(
        color='blue',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[target_center[0], center[0]], 
    y=np.r_[target_center[1], center[1]], 
    z=np.r_[target_center[2], center[2]],
    mode="lines",
    line=dict(
        color='red',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))


circle_points = get_circle_points(center, target_center, plane_center, radius_factor=0.99)


# Adding sphere outline
data.append(go.Scatter3d(
    x=np.r_[circle_points[:,0], circle_points[0,0]], 
    y=np.r_[circle_points[:,1], circle_points[0,1]], 
    z=np.r_[circle_points[:,2], circle_points[0,2]],
    mode="lines",
    line=dict(
        color='black',
        width=4,
        # size=10,
        dash="dash"
    ),
    showlegend=False
    
))

# Adding plane point
data.append(
    go.Scatter3d(
    x=[plane_center[0]], 
    y=[plane_center[1]], 
    z=[plane_center[2]],
    mode="markers",
    marker=dict(
        color="blue",
        symbol="x",
        size=3
    ),
    showlegend=False
    
)
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=1.45, y=1.45, z=0.7)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
        ),
        scene_camera = camera
    )
)

# fig.update_layout()

fig.show()
fig.write_image("./plane_to_plane.svg")

### Plane to plane boundaries

In [3]:
### Inscribed circle field plane to plane
data = []

base_square = np.array([
    [0,0,-0.02],
    [1,0,-0.02],
    [1,1,-0.02],
    [0,1,-0.02],
])
base_tris = np.array([
    [0,1,2],
    [2,3,0]
])

# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

triangle = np.array([
    [0.2, 0.15, 0.15],
    [0.5, 0.15, 0.8],
    [0.8, 0.15, 0.15],
])
tri = np.array([[0,1,2]])

# Adding triangle
data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    
    i = tri[:,0],
    j = tri[:,1],
    k = tri[:,2],
    color="white",
    showlegend=False

))

#Adding triangle borders and points
data.append(go.Scatter3d(
    x=np.r_[triangle[:,0], triangle[0,0]], 
    y=np.r_[triangle[:,1], triangle[0,1]], 
    z=np.r_[triangle[:,2], triangle[0,2]],
    mode="markers+lines",
    marker=dict(
        color="red",
        size=4
    ),
    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
    
))

center = np.array([0.5,0.5,0.35])

plane_center = [0.5, 0.5, 0]

target_center = [0.5, 0.15, 0.35]

# Adding plane and trigangle normals

data.append(go.Scatter3d(
    x=np.r_[plane_center[0], center[0]], 
    y=np.r_[plane_center[1], center[1]], 
    z=np.r_[plane_center[2], center[2]],
    mode="lines",
    line=dict(
        color='blue',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[target_center[0], center[0]], 
    y=np.r_[target_center[1], center[1]], 
    z=np.r_[target_center[2], center[2]],
    mode="lines",
    line=dict(
        color='red',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))


circle_points = get_circle_points(center, target_center, plane_center, radius_factor=0.99)




# Adding plane point
data.append(
    go.Scatter3d(
        x=[plane_center[0]], 
        y=[plane_center[1]], 
        z=[plane_center[2]],
        mode="markers",
        marker=dict(
            color="blue",
            symbol="x",
            size=3
        ),
        showlegend=False
    )
)


boundary_centers = np.array([
    [0.2, 0.3, 0.15],
    [0.5, 0.95, 0.8],
    [0.8, 0.3, 0.15],
])

boundary_base = np.array([
    [0.2, 0.3, 0],
    [0.5, 0.95,0],
    [0.8, 0.3, 0],
])

tri_boundary_dirs = np.stack((triangle, boundary_centers), axis=1)
# print(tri_boundary_dirs[:,:,2])


data.append(
    go.Scatter3d(
        x=tri_boundary_dirs[0,:,0], 
        y=tri_boundary_dirs[0,:,1], 
        z=tri_boundary_dirs[0,:,2],
        mode="lines",
        line=dict(
            color='red',
            width=3,
            # size=10,
            # dash="dot"
        ),
        showlegend=False
    )
)
data.append(
    go.Scatter3d(
        x=tri_boundary_dirs[1,:,0], 
        y=tri_boundary_dirs[1,:,1], 
        z=tri_boundary_dirs[1,:,2],
        mode="lines",
        line=dict(
            color='red',
            width=3,
            # size=10,
            # dash="dot"
        ),
        showlegend=False
    )
)
data.append(
    go.Scatter3d(
        x=tri_boundary_dirs[2,:,0], 
        y=tri_boundary_dirs[2,:,1], 
        z=tri_boundary_dirs[2,:,2],
        mode="lines",
        line=dict(
            color='red',
            width=3,
            # size=10,
            # dash= "dot"
        ),
        showlegend=False
    )
)

tri_plane_dirs = np.stack((boundary_base, boundary_centers), axis=1)

data.append(
    go.Scatter3d(
        x=tri_plane_dirs[0,:,0], 
        y=tri_plane_dirs[0,:,1], 
        z=tri_plane_dirs[0,:,2],
        mode="lines",
        line=dict(
            color='blue',
            width=3,
            # size=10,
            # dash="dot"
        ),
        showlegend=False
    )
)
data.append(
    go.Scatter3d(
        x=tri_plane_dirs[1,:,0], 
        y=tri_plane_dirs[1,:,1], 
        z=tri_plane_dirs[1,:,2],
        mode="lines",
        line=dict(
            color='blue',
            width=3,
            # size=10,
            # dash="dot"
        ),
        showlegend=False
    )
)
data.append(
    go.Scatter3d(
        x=tri_plane_dirs[2,:,0], 
        y=tri_plane_dirs[2,:,1], 
        z=tri_plane_dirs[2,:,2],
        mode="lines",
        line=dict(
            color='blue',
            width=3,
            # size=10,
            # dash= "dot"
        ),
        showlegend=False
    )
)

data.append(go.Scatter3d(
    x=np.r_[boundary_base[:,0],boundary_base[0,0]], 
    y=np.r_[boundary_base[:,1],boundary_base[0,1]], 
    z=np.r_[boundary_base[:,2],boundary_base[0,2]],
    mode="markers+lines",
    marker=dict(
        color="red",
        size=4
    ),
    line=dict(
        color='green',
        width=2
    ),
    showlegend=False
    
))


camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=1.45, y=1.45, z=0.7)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
        ),
        scene_camera = camera
    )
)
fig.show()
fig.write_image("./plane_boundaries.svg")

### Plane to edge


In [4]:


### Inscribed circle field plane to plane
data = []

base_square = np.array([
    [0,0,-0.02],
    [1,0,-0.02],
    [1,1,-0.02],
    [0,1,-0.02],
])
base_tris = np.array([
    [0,1,2],
    [2,3,0]
])

# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

triangle = np.array([
    [0.2, 0.35, 0.15],
    [0.5, 0.35, 0.8],
    [0.8, 0.35, 0.35],
])
tri = np.array([[0,1,2]])

# Adding triangle
data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    
    i = tri[:,0],
    j = tri[:,1],
    k = tri[:,2],
    color="white",
    showlegend=False

))

#Adding triangle borders and points
data.append(go.Scatter3d(
    x=np.r_[triangle[:,0], triangle[0,0]], 
    y=np.r_[triangle[:,1], triangle[0,1]], 
    z=np.r_[triangle[:,2], triangle[0,2]],
    mode="markers+lines",
    marker=dict(
        color="red",
        size=4
    ),
    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
    
))


plane_center = [0.5, 0.5, 0]
line_dir = (triangle[2]-triangle[0])/np.linalg.norm(triangle[2]-triangle[0])
dist = line_distance(np.array(plane_center), np.array([0,0,1]), triangle[0], line_dir)

center = np.array([0.5,0.5, dist[0]])




target_center = triangle[0] + np.dot(line_dir, center-triangle[0])*line_dir



sphere_points = get_sphere_points(center, dist*0.98)

# Adding sphere
data.append(go.Surface(
    x = sphere_points[0],
    y = sphere_points[1],
    z = sphere_points[2],

    colorscale=[[0, "cyan"], [1, "black"]],
    surfacecolor = np.zeros(sphere_points[0].shape),
    # color = "cyan",
    opacity = 0.2,
    showscale=False,
))




# Adding plane and trigangle normals

data.append(go.Scatter3d(
    x=np.r_[plane_center[0], center[0]], 
    y=np.r_[plane_center[1], center[1]], 
    z=np.r_[plane_center[2], center[2]],
    mode="lines",
    line=dict(
        color='blue',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[target_center[0], center[0]], 
    y=np.r_[target_center[1], center[1]], 
    z=np.r_[target_center[2], center[2]],
    mode="lines",
    line=dict(
        color='red',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

circle_points = get_circle_points(np.array(center), np.array(target_center), np.array(plane_center), radius_factor=0.99)
# Adding sphere outline
data.append(go.Scatter3d(
    x=np.r_[circle_points[:,0], circle_points[0,0]], 
    y=np.r_[circle_points[:,1], circle_points[0,1]], 
    z=np.r_[circle_points[:,2], circle_points[0,2]],
    mode="lines",
    line=dict(
        color='black',
        width=4,
        # size=10,
        dash="dash"
    ),
    showlegend=False
    
))

# Adding plane point
data.append(
    go.Scatter3d(
    x=[plane_center[0]], 
    y=[plane_center[1]], 
    z=[plane_center[2]],
    mode="markers",
    marker=dict(
        color="blue",
        symbol="x",
        size=3
    ),
    showlegend=False
    )
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=1.45, y=1.45, z=0.7)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
        ),
        scene_camera = camera
    )
)

# fig.update_layout()

fig.show()
fig.write_image("./plane_to_edge.svg")

### Plane to edge boundaries


In [26]:


### Inscribed circle field plane to plane
data = []

base_square = np.array([
    [0,0,-0.02],
    [1,0,-0.02],
    [1,1,-0.02],
    [0,1,-0.02],
])
base_tris = np.array([
    [0,1,2],
    [2,3,0]
])

# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

triangle = np.array([
    [-.6 + 0.2, 0.35, 0.15],
    [-.3 + 0.2, 0.35, 0.8],
    [0 + 0.2, 0.35, 0.35],
])
tri = np.array([[0,1,2]])

# Adding triangle
data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    
    i = tri[:,0],
    j = tri[:,1],
    k = tri[:,2],
    color="white",
    showlegend=False

))

#Adding triangle borders and points
data.append(go.Scatter3d(
    x=np.r_[triangle[:,0], triangle[0,0]], 
    y=np.r_[triangle[:,1], triangle[0,1]], 
    z=np.r_[triangle[:,2], triangle[0,2]],
    mode="markers+lines",
    marker=dict(
        color="red",
        size=4
    ),
    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
    
))


plane_center = [0.5, 0.5, 0]
line_dir = (triangle[2]-triangle[0])/np.linalg.norm(triangle[2]-triangle[0])
dist = line_distance(np.array(plane_center), np.array([0,0,1]), triangle[0], line_dir)

center = np.array([0.5,0.5, dist[0]])




target_center = triangle[0] + np.dot(line_dir, center-triangle[0])*line_dir



sphere_points = get_sphere_points(center, dist*0.98)

# Adding sphere
data.append(go.Surface(
    x = sphere_points[0],
    y = sphere_points[1],
    z = sphere_points[2],

    colorscale=[[0, "cyan"], [1, "black"]],
    surfacecolor = np.zeros(sphere_points[0].shape),
    # color = "cyan",
    opacity = 0.2,
    showscale=False,
))




# Adding plane and trigangle normals

data.append(go.Scatter3d(
    x=np.r_[plane_center[0], center[0]], 
    y=np.r_[plane_center[1], center[1]], 
    z=np.r_[plane_center[2], center[2]],
    mode="lines",
    line=dict(
        color='blue',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[target_center[0], center[0]], 
    y=np.r_[target_center[1], center[1]], 
    z=np.r_[target_center[2], center[2]],
    mode="lines",
    line=dict(
        color='red',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

circle_points = get_circle_points(np.array(center), np.array(target_center), np.array(plane_center), radius_factor=0.99)
# Adding sphere outline
data.append(go.Scatter3d(
    x=np.r_[circle_points[:,0], circle_points[0,0]], 
    y=np.r_[circle_points[:,1], circle_points[0,1]], 
    z=np.r_[circle_points[:,2], circle_points[0,2]],
    mode="lines",
    line=dict(
        color='black',
        width=4,
        # size=10,
        dash="dash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[triangle[2,0], target_center[0]], 
    y=np.r_[triangle[2,1], target_center[1]], 
    z=np.r_[triangle[2,2], target_center[2]],
    mode="lines",
    line=dict(
        color='black',
        width=4,
        # size=10,
        dash="longdash"
    ),
    showlegend=False
    
))

# Adding plane point
data.append(
    go.Scatter3d(
    x=[plane_center[0]], 
    y=[plane_center[1]], 
    z=[plane_center[2]],
    mode="markers",
    marker=dict(
        color="blue",
        symbol="x",
        size=3
    ),
    showlegend=False
    )
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0., y=0, z=-0.1),
    eye=dict(x=0, y=1.3, z=0.5)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),#, range=[-., 1.5]),
            yaxis=dict(visible=False),#, range=[-.5, 1.5]),
            zaxis=dict(visible=False),#, range=[-.05, 2.05]),
            aspectratio=dict(z=3)
        ),
        scene_camera = camera
    )
)

# fig.update_layout()

fig.show()
fig.write_image("./plane_to_edge_boundaries_1.svg")



In [22]:


### Inscribed circle field plane to plane
data = []

base_square = np.array([
    [0,0,-0.02],
    [1,0,-0.02],
    [1,1,-0.02],
    [0,1,-0.02],
])
base_tris = np.array([
    [0,1,2],
    [2,3,0]
])

# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

triangle = np.array([
    [-.6 + 0.2, 0.35, 0.15],
    [-.3 + 0.2, 0.35, 0.8],
    [0 + 0.2, 0.35, 0.35],
])
tri = np.array([[0,1,2]])

# Adding triangle
data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    
    i = tri[:,0],
    j = tri[:,1],
    k = tri[:,2],
    color="white",
    showlegend=False

))

#Adding triangle borders and points
data.append(go.Scatter3d(
    x=np.r_[triangle[:,0], triangle[0,0]], 
    y=np.r_[triangle[:,1], triangle[0,1]], 
    z=np.r_[triangle[:,2], triangle[0,2]],
    mode="markers+lines",
    marker=dict(
        color="red",
        size=4
    ),
    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
    
))


plane_center = [0.5, 0.5, 0]
line_dir = (triangle[2]-triangle[1])/np.linalg.norm(triangle[2]-triangle[1])
dist = line_distance(np.array(plane_center), np.array([0,0,1]), triangle[1], line_dir)

center = np.array([0.5,0.5, dist[0]])




target_center = triangle[1] + np.dot(line_dir, center-triangle[1])*line_dir



sphere_points = get_sphere_points(center, dist*0.98)

# Adding sphere
data.append(go.Surface(
    x = sphere_points[0],
    y = sphere_points[1],
    z = sphere_points[2],

    colorscale=[[0, "cyan"], [1, "black"]],
    surfacecolor = np.zeros(sphere_points[0].shape),
    # color = "cyan",
    opacity = 0.2,
    showscale=False,
))




# Adding plane and trigangle normals

data.append(go.Scatter3d(
    x=np.r_[plane_center[0], center[0]], 
    y=np.r_[plane_center[1], center[1]], 
    z=np.r_[plane_center[2], center[2]],
    mode="lines",
    line=dict(
        color='blue',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[target_center[0], center[0]], 
    y=np.r_[target_center[1], center[1]], 
    z=np.r_[target_center[2], center[2]],
    mode="lines",
    line=dict(
        color='red',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

circle_points = get_circle_points(np.array(center), np.array(target_center), np.array(plane_center), radius_factor=0.99)
# Adding sphere outline
data.append(go.Scatter3d(
    x=np.r_[circle_points[:,0], circle_points[0,0]], 
    y=np.r_[circle_points[:,1], circle_points[0,1]], 
    z=np.r_[circle_points[:,2], circle_points[0,2]],
    mode="lines",
    line=dict(
        color='black',
        width=4,
        # size=10,
        dash="dash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[triangle[2,0], target_center[0]], 
    y=np.r_[triangle[2,1], target_center[1]], 
    z=np.r_[triangle[2,2], target_center[2]],
    mode="lines",
    line=dict(
        color='black',
        width=4,
        # size=10,
        dash="longdash"
    ),
    showlegend=False
    
))

# Adding plane point
data.append(
    go.Scatter3d(
    x=[plane_center[0]], 
    y=[plane_center[1]], 
    z=[plane_center[2]],
    mode="markers",
    marker=dict(
        color="blue",
        symbol="x",
        size=3
    ),
    showlegend=False
    )
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=-0.1),
    eye=dict(x=0, y=1.3, z=0.5)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
        ),
        scene_camera = camera
    )
)

# fig.update_layout()

fig.show()
fig.write_image("./plane_to_edge_boundaries_2.svg")

### Plane to point 

In [24]:


### Inscribed circle field plane to plane
data = []

base_square = np.array([
    [0,0,-0.02],
    [1,0,-0.02],
    [1,1,-0.02],
    [0,1,-0.02],
])
base_tris = np.array([
    [0,1,2],
    [2,3,0]
])

# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

triangle = np.array([
    [-.6 + 0.2, 0.35, 0.15],
    [-.3 + 0.2, 0.35, 0.8],
    [0 + 0.2, 0.35, 0.35],
])
tri = np.array([[0,1,2]])

# Adding triangle
data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    
    i = tri[:,0],
    j = tri[:,1],
    k = tri[:,2],
    color="white",
    showlegend=False

))

#Adding triangle borders and points
data.append(go.Scatter3d(
    x=np.r_[triangle[:,0], triangle[0,0]], 
    y=np.r_[triangle[:,1], triangle[0,1]], 
    z=np.r_[triangle[:,2], triangle[0,2]],
    mode="markers+lines",
    marker=dict(
        color="red",
        size=4
    ),
    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
    
))


plane_center = [0.5, 0.5, 0]
# line_dir = (triangle[2]-triangle[1])/np.linalg.norm(triangle[2]-triangle[1])
dist = point_distance(np.array(plane_center), np.array([0,0,1]), triangle[2]) 

center = np.array([0.5,0.5, dist])


target_center = triangle[2]



sphere_points = get_sphere_points(center, dist*0.98)

# Adding sphere
data.append(go.Surface(
    x = sphere_points[0],
    y = sphere_points[1],
    z = sphere_points[2],

    colorscale=[[0, "cyan"], [1, "black"]],
    surfacecolor = np.zeros(sphere_points[0].shape),
    # color = "cyan",
    opacity = 0.2,
    showscale=False,
))




# Adding plane and trigangle normals

data.append(go.Scatter3d(
    x=np.r_[plane_center[0], center[0]], 
    y=np.r_[plane_center[1], center[1]], 
    z=np.r_[plane_center[2], center[2]],
    mode="lines",
    line=dict(
        color='blue',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

data.append(go.Scatter3d(
    x=np.r_[target_center[0], center[0]], 
    y=np.r_[target_center[1], center[1]], 
    z=np.r_[target_center[2], center[2]],
    mode="lines",
    line=dict(
        color='red',
        width=4,
        # size=10,
        # dash="longdash"
    ),
    showlegend=False
    
))

circle_points = get_circle_points(np.array(center), np.array(target_center), np.array(plane_center), radius_factor=0.99)
# Adding sphere outline
data.append(go.Scatter3d(
    x=np.r_[circle_points[:,0], circle_points[0,0]], 
    y=np.r_[circle_points[:,1], circle_points[0,1]], 
    z=np.r_[circle_points[:,2], circle_points[0,2]],
    mode="lines",
    line=dict(
        color='black',
        width=4,
        # size=10,
        dash="dash"
    ),
    showlegend=False
    
))


# Adding plane point
data.append(
    go.Scatter3d(
    x=[plane_center[0]], 
    y=[plane_center[1]], 
    z=[plane_center[2]],
    mode="markers",
    marker=dict(
        color="blue",
        symbol="x",
        size=3
    ),
    showlegend=False
    )
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=-0.1),
    eye=dict(x=0, y=1.3, z=0.5)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
        ),
        scene_camera = camera
    )
)

# fig.update_layout()

fig.show()
fig.write_image("./plane_to_point.svg")

### Voronoi Construction Steps


In [18]:
data = []

base_square = np.array([
    [0,0,0],
    [1,0,0],
    [1,1,0],
    [0,1,0],
])

base_tris = np.array([
    [0,1,2],
    [2,3,0]
])


# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=.9, y=.9, z=2)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False, range = [-.5,.5]),
            aspectratio=dict(x=1.3, y=1.3, z=1.3)
        ),
        scene_camera = camera
    )
)

fig.show()
fig.write_image("./origin_shape.svg")

In [19]:
data = []


gmsh.initialize()
gmsh.model.add("Basic triangulation")

base_points = []
for point in base_square:
    base_points.append(gmsh.model.geo.add_point(point[0], point[1], point[2], 0.35))

base_edges = []
for i in range(len(base_points)):
    base_edges.append(gmsh.model.geo.add_line(base_points[i], base_points[(i+1)%len(base_points)]))

base_loop = gmsh.model.geo.add_curve_loop(base_edges)
base_plane = gmsh.model.geo.add_plane_surface([base_loop])

gmsh.model.geo.synchronize()

gmsh.model.mesh.generate(2)

gmsh.model.mesh.create_faces()

_, node_coords, *_ = gmsh.model.mesh.get_nodes()
_, tri_nodes, *_ = gmsh.model.mesh.get_all_faces(3)
node_coords = node_coords.reshape(-1,3)
tri_nodes = tri_nodes.reshape(-1,3)-1

# print(node_coords)

ii, jj, kk = tri_nodes.T
# print(ii)
data.append(go.Mesh3d(
    x = node_coords[:,0],
    y = node_coords[:,1],
    z = node_coords[:,2],
    i = ii,
    j = jj,
    k = kk,
    color='white'
))



tri_x = np.vstack((node_coords[ii,0], node_coords[jj,0], node_coords[kk,0], np.repeat(None, ii.shape[0]))).T.flatten() 
tri_y = np.vstack((node_coords[ii,1], node_coords[jj,1], node_coords[kk,1], np.repeat(None, ii.shape[0]))).T.flatten() 
tri_z = np.vstack((node_coords[ii,2], node_coords[jj,2], node_coords[kk,2], np.repeat(None, ii.shape[0]))).T.flatten() 



data.append(go.Scatter3d(
        x=tri_x,
        y=tri_y, 
        z=tri_z,
        mode="lines",

        line=dict(
            color='black',
            width=2
        ),
        showlegend=False
    )
)
camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=.9, y=.9, z=2)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False, range = [-.5,.5]),
            aspectratio=dict(x=1.3, y=1.3, z=1.3)
        ),
        scene_camera = camera
    )
)
fig.show()
fig.write_image("./triangulated.svg")

### Vertex spheres



In [22]:
data = []




radii = np.zeros(node_coords.shape[0])

for tri_node_ids in tri_nodes:
    dists = np.mean(np.sqrt(np.sum((node_coords[tri_node_ids] - node_coords[np.roll(tri_node_ids,-1)])**2, axis=-1)))
    radii[tri_node_ids] = np.maximum(radii[tri_node_ids], dists)

radii = radii * 0.7

triangle_focus = 0
distance = 10
for i, tri in enumerate(tri_nodes):
    mean = np.mean(node_coords[tri], axis=0)
    dist =np.linalg.norm(np.array([0.5,0.5,0]) - mean)
    if dist < distance:
        distance = dist
        triangle_focus = i

for node_id, radius in enumerate(radii):
    if node_id not in tri_nodes[triangle_focus]:
        continue
    sphere_points = get_sphere_points(node_coords[node_id], radius, 200, 100)

    # Adding sphere
    data.append(go.Surface(
        x = sphere_points[0],
        y = sphere_points[1],
        z = sphere_points[2],

        colorscale=[[0, "cyan"], [1, "black"]],
        surfacecolor = np.zeros(sphere_points[0].shape),
        # color = "cyan",
        opacity = 0.2,
        showscale=False,
    ))
    # data.append()

inner, outer = sphere_intersections(node_coords[tri_nodes[triangle_focus]].reshape(-1,3,3), radii[tri_nodes[triangle_focus]].reshape(-1,3))
for vertex in node_coords[tri_nodes[triangle_focus]]:
    circle_points = get_circle_points(vertex, inner[0], outer[0], radius_factor=0.99)


    # Adding sphere outline
    data.append(go.Scatter3d(
        x=np.r_[circle_points[:,0], circle_points[0,0]], 
        y=np.r_[circle_points[:,1], circle_points[0,1]], 
        z=np.r_[circle_points[:,2], circle_points[0,2]],
        mode="lines",
        line=dict(
            color='black',
            width=4,
            # size=10,
            dash="dash"
        ),
        showlegend=False
        
    ))

# print(node_coords)

ii, jj, kk = tri_nodes.T
# print(ii)
data.append(go.Mesh3d(
    x = node_coords[:,0],
    y = node_coords[:,1],
    z = node_coords[:,2],
    i = ii,
    j = jj,
    k = kk,
    color='white'
))

data.append(go.Mesh3d(
    x = node_coords[tri_nodes[triangle_focus],0],
    y = node_coords[tri_nodes[triangle_focus],1],
    z = node_coords[tri_nodes[triangle_focus],2],
    i = [0],
    j = [1],
    k = [2],
    color='cyan'
))
print(node_coords[tri_nodes[triangle_focus],0])
print(node_coords[tri_nodes[triangle_focus],1])
print(node_coords[tri_nodes[triangle_focus],2])
tri_x = np.vstack((node_coords[ii,0], node_coords[jj,0], node_coords[kk,0], np.repeat(None, ii.shape[0]))).T.flatten() 
tri_y = np.vstack((node_coords[ii,1], node_coords[jj,1], node_coords[kk,1], np.repeat(None, ii.shape[0]))).T.flatten() 
tri_z = np.vstack((node_coords[ii,2], node_coords[jj,2], node_coords[kk,2], np.repeat(None, ii.shape[0]))).T.flatten() 



data.append(go.Scatter3d(
    x=tri_x,
    y=tri_y, 
    z=tri_z,
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))

data.append(
    go.Scatter3d(
        x=np.r_[outer[0,0], inner[0,0]], 
        y=np.r_[outer[0,1], inner[0,1]], 
        z=np.r_[outer[0,2], inner[0,2]],
        mode="markers",
        marker=dict(
            color="red",
            # symbol="x",
            size=5
        ),
        showlegend=False
    
    )
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=.9, y=.9, z=2)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False, range = [-.5,.5]),
            aspectratio=dict(x=1.3, y=1.3, z=1.3)
        ),
        scene_camera = camera
    )
)
fig.show()
fig.write_image("./spheres.svg")

[0.71132487 0.28867513 0.5       ]
[0.5        0.5        0.24743992]
[0. 0. 0.]


### Voronoi


In [11]:
data = []


inner, outer = sphere_intersections(node_coords[tri_nodes].reshape(-1,3,3), radii[tri_nodes].reshape(-1,3))

all_sites = np.vstack((inner, outer))

voronoi = Voronoi(all_sites)

vertices = voronoi.vertices

ridges = voronoi.ridge_vertices


for ridge in ridges:
    valid_indices = np.delete(ridge, np.where(ridge == -1)[0])
    data.append(go.Scatter3d(
        x=np.r_[vertices[valid_indices, 0], vertices[valid_indices[0], 0]],
        y=np.r_[vertices[valid_indices, 1], vertices[valid_indices[0], 1]], 
        z=np.r_[vertices[valid_indices, 2], vertices[valid_indices[0], 2]],
        mode="lines",

        line=dict(
            color='black',
            width=2
        ),
        showlegend=False
    )
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=.9, y=.9, z=2)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
        ),
        scene_camera = camera
    )
)
fig.show()
fig.write_image("./Voronoi.svg")

In [4]:


base_square = np.array([
    [0,0,0],
    [1,0,0],
    [1,1,0],
    [0,1,0],
])


skew_plane = np.array([
    [0,0,.5],
    [1,0,.5],
    [1,1,.5],
    [0,1,.5],
])
skew_edges = np.array([
    [0,1],
    [1,2],
    [2,3],
    [3,0]
])


gmsh.initialize()
gmsh.model.add("plane_1")

base_points = []
for point in base_square:
    base_points.append(gmsh.model.geo.add_point(point[0], point[1], point[2], 0.35))

base_edges = []
for i in range(len(base_points)):
    base_edges.append(gmsh.model.geo.add_line(base_points[i], base_points[(i+1)%len(base_points)]))

base_loop = gmsh.model.geo.add_curve_loop(base_edges)
base_plane = gmsh.model.geo.add_plane_surface([base_loop])


# gmsh.option.setNumber("Mesh.MeshSizeExtendFromBoundary", 0)
# gmsh.option.setNumber("Mesh.MeshSizeFromPoints", 0)
# gmsh.option.setNumber("Mesh.MeshSizeFromCurvature", 0)

triangle_ids = base_tris = np.array([
    [0,1,2],
    [2,3,0]
])

skew_triangle_coords = skew_plane[triangle_ids]

# Sets up the inscribed circle size field
current = os.getcwd()
density_field = triangle_inscribed_circle_field(skew_triangle_coords, np.array([0,0,1]), 10, data_path=os.path.join(current, "skew_planes.npy"))

gmsh.model.mesh.field.setAsBackgroundMesh(density_field)

gmsh.model.geo.synchronize()
gmsh.model.mesh.generate(2)
gmsh.model.mesh.create_faces()
gmsh.fltk.run()

_, node_coords, *_ = gmsh.model.mesh.get_nodes()
_, tri_nodes, *_ = gmsh.model.mesh.get_all_faces(3)
node_coords = node_coords.reshape(-1,3)
tri_nodes = tri_nodes.reshape(-1,3)-1

# skew__tris = np.array([
#     [0,1,2],
#     [2,3,0]
# ])


# CEC = ConstrainedEdgeCollection()

# CEC.add_vertices(np.vetack(base_square, skew_plane))
# CEC.add_edges(np.vstack(base_edges, skew_edges + 4))
# CEC.add_face(np.array([0,1,2,3]))
# CEC.add_face(np.array([4,5,6,7]))
# CEC.

In [43]:




triangle = np.array([
    [0,0,0],
    [1,0,0],
    [.5,np.sqrt(3)/2,0],
])

comp_point = np.array([1.5,0.5*3**0.5,0])

points = np.array([
    [0.5, 1/(2*3**0.5), -1/(2*3**0.5)],
    [0.5, 1/(2*3**0.5), 1/(2*3**0.5)],
    [1, 0.5*3**0.5-1/(2*3**0.5), 1/(2*3**0.5)]
])

plane_center = np.array([
    [0.5, 1/(2*3**0.5), 0],
    (points[1] + points[2])/2
])
data = []
data.append(
    go.Scatter3d(
        x = np.r_[triangle[1,0], comp_point[0], triangle[2,0]],
        y = np.r_[triangle[1,1], comp_point[1], triangle[2,1]],
        z = np.r_[triangle[1,2], comp_point[2], triangle[2,2]],

        mode = "lines",
        line=dict(
            color='grey',
            width=2
        ),
        showlegend=False
    )        
)
data.append(
    go.Scatter3d(
        x = np.r_[triangle[:,0], triangle[0,0]],
        y = np.r_[triangle[:,1], triangle[0,1]],
        z = np.r_[triangle[:,2], triangle[0,2]],

        mode = "lines",
        line=dict(
            color='black',
            width=2
        ),
        showlegend=False
    )        
)


data.append(
    go.Scatter3d(
        x = np.r_[plane_center[0,0], points[1,0], plane_center[1,0]],
        y = np.r_[plane_center[0,1], points[1,1], plane_center[1,1]],
        z = np.r_[plane_center[0,2], points[1,2], plane_center[1,2]],

        mode = "lines",
        line=dict(
            color='red',
            width=5,
            # dash = ,
        ),
        showlegend=False
    )        
)

data.append(
    go.Scatter3d(
        x = np.r_[triangle[0,0], points[1,0]],
        y = np.r_[triangle[0,1], points[1,1]],
        z = np.r_[triangle[0,2], points[1,2]],

        mode = "lines",
        line=dict(
            color='blue',
            width=5,
            dash = "longdash",
        ),
        showlegend=False
    )        
)

data.append(
    go.Scatter3d(
        x = points[:,0],
        y = points[:,1],
        z = points[:,2],

        mode = "markers",
        # line=dict(
        #     color='black',
        #     width=2
        # ),
        marker = dict(
            size = 5,
            color = "grey",
        ),
        showlegend=False
    )        
)

data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    i = [0],
    j = [1],
    k = [2],
    color="cyan",
    opacity=0.3
))
# plane_center = np.array([0.5, 1/(2*3**0.5), 0])
data.append(
    go.Scatter3d(
    x=[plane_center[0, 0]], 
    y=[plane_center[0, 1]], 
    z=[plane_center[0, 2]],
    mode="markers",
    marker=dict(
        color="black",
        symbol="x",
        size=3
    ),
    showlegend=False
    )
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=-.15, y=0, z=0),
    eye=dict(x=.5, y=-1.5, z=.5)
)



fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False, range=[0,1.5]),
            yaxis=dict(visible=False, range=[0,1.5]),
            zaxis=dict(visible=False, range=[-.75,.75]),
            aspectratio=dict(x=1.3, y=1.3, z=1.3)
        ),
        scene_camera = camera
    )
)
fig.show()
fig.write_image("./centroidal_distances.svg")


In [53]:

### Inscribed circle field plane to plane
data = []

base_square = np.array([
    [0,0,-0.02],
    [1,0,-0.02],
    [1,1,-0.02],
    [0,1,-0.02],
])
base_tris = np.array([
    [0,1,2],
    [2,3,0]
])
triangle = np.array([
    [0.6, 0.6, 0.2],
    [0.4, 0.6, 0.2],
    [0.4, 0.3, 0.2],
])
tri = np.array([[0,1,2]])

# Adding base plane
data.append(go.Mesh3d(
    x = base_square[:,0],
    y = base_square[:,1],
    z = base_square[:,2],
    
    i = base_tris[:,0],
    j = base_tris[:,1],
    k = base_tris[:,2],
    color = "white"
))

# Adding base square border
data.append(go.Scatter3d(
    x=np.r_[base_square[:,0], base_square[0,0]], 
    y=np.r_[base_square[:,1], base_square[0,1]], 
    z=np.r_[base_square[:,2], base_square[0,2]],
    mode="lines",

    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
))


# Adding triangle
data.append(go.Mesh3d(
    x = triangle[:,0],
    y = triangle[:,1],
    z = triangle[:,2],
    
    i = tri[:,0],
    j = tri[:,1],
    k = tri[:,2],
    color="white",
    showlegend=False

))

#Adding triangle borders and points
data.append(go.Scatter3d(
    x=np.r_[triangle[:,0], triangle[0,0]], 
    y=np.r_[triangle[:,1], triangle[0,1]], 
    z=np.r_[triangle[:,2], triangle[0,2]],
    mode="lines",
    line=dict(
        color='black',
        width=2
    ),
    showlegend=False
    
))


camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=-1.1, y=1.1, z=0.9)
)

fig = go.Figure(
    data = data,
    layout=dict(
        margin=dict(l=0,r=0,b=0,t=0),
        width=1000,
        height = 625,
        scene = dict( 
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False, range=[-.5,.5]),
        ),
        scene_camera = camera
    )
)

# fig.update_layout()

fig.show()
fig.write_image("./ISD_Test_Scene.svg")